In [1]:
from aaredaq.devices import BeamlineDevices
from aaredaqlib.beamline import MXBeamline

ModuleNotFoundError: No module named 'aaredaq'

In [ ]:
from epics import PV
import numpy as np
import time
import matplotlib.pyplot as plt
from scipy.optimize import curve_fit
from scipy.signal import peak_widths, find_peaks
from scipy import asarray as ar,exp

In [ ]:
d = BeamlineDevices(MXBeamline.X06DA)
b = MXBeamline.X06DA
beamline = b.value.upper()

In [ ]:
def gaus(x, *p):
    A, mu, sigma = p
    return A * np.exp(-(x-mu)**2/(2.*sigma**2))

def sigmoid(x, *p):
    L, x0, k, b = p
    return L / (1 + np.exp(-k * (x -x0))) + b

def unpack_data(data):
    x_vals, y_vals = zip(*data)
    x_vals = list(x_vals)
    y_vals = list(y_vals)
    return x_vals, y_vals

def sigmoid_fit(x_vals, y_vals):
    L_guess = np.max(y_vals)
    b_guess = np.min(y_vals)
    x0_guess = x_vals[np.argmin(np.abs(y_vals - (L_guess + b_guess) / 2))]
    k_guess = 1 / (x_vals[-1] - x_vals[0])

    s0 = [L_guess, x0_guess, k_guess, b_guess]
    parameters, params_covariance = curve_fit(sigmoid, x_vals, y_vals, p0=s0)
    return parameters

def gauss_fit(x_vals, dydx):
    mean = x_vals[np.argmax(dydx)]
    sigma = (np.max(x_vals) - np.min(x_vals))/4
    A= np.max(dydx)
    dydx[np.isnan(dydx)] = 0

    p0 = [A, mean, sigma]
    parameters, covariance = curve_fit( gaus, x_vals, dydx, p0=p0)
    return parameters

def calc_fwhm(gauss_y, x_vals):
    peaks = find_peaks( gauss_y )
    fwhm_peak = peak_widths( gauss_y, peaks[0], rel_height=0.5 )

    fwhm_str = x_vals[int( round( fwhm_peak[2][0], 0 ))]
    fwhm_end = x_vals[int( round( fwhm_peak[3][0], 0 ))]

    fwhm = fwhm_str - fwhm_end
    fwhm_height = gauss_y[int( round( fwhm_peak[2][0], 0 ))]

    # find 1/e2 peak width
    full_peak = peak_widths( gauss_y, peaks[0], rel_height=0.865 )
    full_str = x_vals[int( round( full_peak[2][0], 0 ))]
    full_end = x_vals[int( round( full_peak[3][0], 0 ))]

    full = full_str - full_end
    full_height = gauss_y[int( round( full_peak[2][0], 0 ))]
    return fwhm, full

In [ ]:
def knife_edge(motor: str, d: BeamlineDevices, beamline: str, steps: int = 40, start: float = 0.0, step_size: float = 0.002, offset: float = 0.0):
    diode = PV(f"{beamline}-ES-BS:READOUT")#X06DA-ES-BS:READOUT
    d.shutter = True
    time.sleep(1.0)

    data = []

    for i in range(steps): #40
        if motor == 'X':
            d.gmx.move(start-offset+step_size*i, wait=True)
            time.sleep(1.0)
            print(f"{d.gmx.value:.3f} {diode.get()}")
            data.append([d.gmx.value, diode.get()])
        else:
            d.gmy.move(start-offset+step_size*i, wait=True)
            time.sleep(1.0)
            print(f"{d.gmy.value:.3f} {diode.get()}")
            data.append([d.gmy.value, diode.get()])

    if motor == 'X':
        d.gmx.move(start, wait=True)
    else:
        d.gmy.move(start, wait=True)

    d.shutter = False
    return data


In [ ]:
def plot_knife_edge(data, motor: str):

    x_vals, y_vals = unpack_data(data)

    plt.plot(x_vals, y_vals, label = 'edge_scan')
    plt.ylabel('Intensity (counts)')
    plt.xlabel('Motor position (mm)')

    params=sigmoid_fit(x_vals, y_vals)

    plt.plot(x_vals, y_vals)
    plt.plot(x_vals, sigmoid(x_vals, *params))
    plt.show()

    y_fit = sigmoid(x_vals, *params)

    dydx = np.gradient(y_fit, x_vals)

    if motor == 'Y':
        dydx=-dydx

    parameters = gauss_fit(x_vals, dydx)

    x0_op = parameters[1]
    sigma_op = parameters[2]
    print(parameters)

    gauss_y = gaus(x_vals,*parameters)
    fwhm = np.abs(2*np.sqrt(2*np.log(2))*sigma_op)
    print(f"Manually calculated FWHM to {fwhm} mm")
    plt.plot(x_vals, dydx, label = 'derivative')
    plt.plot(x_vals, gauss_y,label='Gaussian fit',color ='orange')
    plt.fill_between(x_vals,gauss_y,color='orange',alpha=0.5)

    try:
        fwhm, full = calc_fwhm(gauss_y, x_vals)
        print( "Scipy calculated FWHM = {0} mm".format( fwhm ) )
        print( "Scipy calculated 1/e2 = {0} mm".format( full ) )
    except:
        print('scipy peak finding failed')

    plt.axvspan(x0_op+fwhm/2,x0_op-fwhm/2, color='green', alpha=0.75, lw=0, label='FWHM = {0} mm'.format(fwhm))
    plt.legend()
    plt.show()
    #plt.savefig(output_name+filename.split('/')[-1]+'FWHM_{0}.png'.format(fwhm))

In [ ]:
x_data=knife_edge(motor='X', d=d, beamline=beamline, steps=40, start=-17.834, step_size=0.002, offset=0.006)
plot_knife_edge(x_data, motor='X')

In [ ]:
y_data=knife_edge(motor='Y', d=d, beamline=beamline, steps=40, start=0.0, step_size=0.002, offset=0.03)
plot_knife_edge(y_data, motor='X')